# Configurations


In [ ]:
!pip install catboost
!pip install ipywidgets
!jupyter nbextension enable --py widgetsnbextension

from datetime import datetime
import numpy as np
import pandas as pd
from tqdm import tqdm
import json
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import normalize
import seaborn as sns
import re
import lightgbm as lgb
import matplotlib.pyplot as plt
import copy
from sklearn.metrics import roc_auc_score, roc_curve

import numpy as np
from numpy.core.fromnumeric import _all_dispatcher
import pandas as pd
import joblib
np.random.seed(2021)
from catboost import CatBoostClassifier
from sklearn.model_selection import train_test_split

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
cd /content/drive/MyDrive

/content/drive/MyDrive


# Data input and processing

## PCA for Combined Features

### pname & stay time

In [ ]:
sgtembedding_train_pname_and_stay_time = pd.read_csv('processed_data/SGT/Combined Features/sgt_train_pname_and_stay_time April 2.csv',index_col=0)
sgtembedding_test_pname_and_stay_time = pd.read_csv('processed_data/SGT/Combined Features/sgt_test_pname_and_stay_time April 2.csv',index_col=0)

del sgtembedding_train_pname_and_stay_time['id']
del sgtembedding_test_pname_and_stay_time['id']

from sklearn.decomposition import PCA
pca = PCA(n_components=300) # 300
pca.fit(sgtembedding_train_pname_and_stay_time)
sgtembedding_train_pname_and_stay_time = pca.transform(sgtembedding_train_pname_and_stay_time)
sgtembedding_test_pname_and_stay_time = pca.transform(sgtembedding_test_pname_and_stay_time)
sgtembedding_train_pname_and_stay_time = pd.DataFrame(data=sgtembedding_train_pname_and_stay_time, columns=[i for i in range(sgtembedding_train_pname_and_stay_time.shape[1])])
sgtembedding_test_pname_and_stay_time = pd.DataFrame(data=sgtembedding_test_pname_and_stay_time, columns=[i for i in range(sgtembedding_test_pname_and_stay_time.shape[1])])

print(np.sum(pca.explained_variance_ratio_))
# 200 0.8464236731438874
# 225 0.8712981619734529
# 250 0.8926073736581202
# 275 0.9102200330779512
# 300 0.9242333936661122
# 325 0.9354327914056986
# 350 0.9451848954115656
# 375 0.9533113024585321
# 400 0.9600

0.9242618639899247


### pname & lagg

In [ ]:
sgtembedding_train_pname_and_lagg = pd.read_csv('processed_data/SGT/Combined Features/sgt_train_pname_and_lagg April 2.csv',index_col=0)
sgtembedding_test_pname_and_lagg = pd.read_csv('processed_data/SGT/Combined Features/sgt_test_pname_and_lagg April 2.csv',index_col=0)

del sgtembedding_train_pname_and_lagg['id']
del sgtembedding_test_pname_and_lagg['id']

from sklearn.decomposition import PCA
pca = PCA(n_components=400)
pca.fit(sgtembedding_train_pname_and_lagg)
sgtembedding_train_pname_and_lagg = pca.transform(sgtembedding_train_pname_and_lagg)
sgtembedding_test_pname_and_lagg = pca.transform(sgtembedding_test_pname_and_lagg)
sgtembedding_train_pname_and_lagg = pd.DataFrame(data=sgtembedding_train_pname_and_lagg, columns=[i for i in range(sgtembedding_train_pname_and_lagg.shape[1])])
sgtembedding_test_pname_and_lagg = pd.DataFrame(data=sgtembedding_test_pname_and_lagg, columns=[i for i in range(sgtembedding_test_pname_and_lagg.shape[1])])

print(np.sum(pca.explained_variance_ratio_))
# 200 0.9076726277753419
# 225 0.9244835167395187
# 250 0.9378354918200023
# 275 0.9485138330511913
# 300 0.9571510509392406
# 325 0.9641164998335948
# 350 0.9702589300917853
# 375 0.975334251468398
# 400 0.9793907032377525

0.979396110832096


### pname & pid

In [ ]:
# sgtembedding_train_pname_and_pid = pd.read_csv('processed_data/SGT/Combined Features/sgt_train_pname_and_pid April 2.csv',index_col=0)

# del sgtembedding_train_pname_and_pid['id']

# n = [i for i in range(200,425,25)]
# from sklearn.decomposition import PCA
# for i in n:
#   pca = PCA(n_components=i)
#   pca.fit(sgtembedding_train_pname_and_pid)
#   print(i,np.sum(pca.explained_variance_ratio_))

In [ ]:
sgtembedding_train_pname_and_pid = pd.read_csv('processed_data/SGT/Combined Features/sgt_train_pname_and_pid April 2.csv',index_col=0)
sgtembedding_test_pname_and_pid = pd.read_csv('processed_data/SGT/Combined Features/sgt_test_pname_and_pid April 2.csv',index_col=0)

del sgtembedding_train_pname_and_pid['id']
del sgtembedding_test_pname_and_pid['id']

from sklearn.decomposition import PCA
pca = PCA(n_components=100)
pca.fit(sgtembedding_train_pname_and_pid)
sgtembedding_train_pname_and_pid = pca.transform(sgtembedding_train_pname_and_pid)
sgtembedding_test_pname_and_pid = pca.transform(sgtembedding_test_pname_and_pid)
sgtembedding_train_pname_and_pid = pd.DataFrame(data=sgtembedding_train_pname_and_pid, columns=[i for i in range(sgtembedding_train_pname_and_pid.shape[1])])
sgtembedding_test_pname_and_pid = pd.DataFrame(data=sgtembedding_test_pname_and_pid, columns=[i for i in range(sgtembedding_test_pname_and_pid.shape[1])])

print(np.sum(pca.explained_variance_ratio_))
# 25 0.9061444586519127
# 50 0.9666048134766424
# 75 0.9827766753774094
# 100 0.9904197739907723
# 125 0.9945328182595236
# 150 0.9966529642704858
# 175 0.9978745240337185
# 200 0.9986426226507609
# 225 0.9991275195693591
# 250 0.9994296992430577
# 275 0.9996408904051497
# 300 0.9997819476356962
# 325 0.9998711125336506
# 350 0.9999304843025515
# 375 0.9999669179226636
# 400 0.9999845491979079

0.9904204757896029


### pname & sid

In [ ]:
# sgtembedding_train_pname_and_sid = pd.read_csv('processed_data/SGT/Combined Features/sgt_train_pname_and_sid April 2.csv',index_col=0)

# del sgtembedding_train_pname_and_sid['id']

# n = [i for i in range(200,425,25)]
# from sklearn.decomposition import PCA
# for i in n:
#   pca = PCA(n_components=i)
#   pca.fit(sgtembedding_train_pname_and_sid)
#   print(i,np.sum(pca.explained_variance_ratio_))

In [ ]:
sgtembedding_train_pname_and_sid = pd.read_csv('processed_data/SGT/Combined Features/sgt_train_pname_and_sid April 2.csv',index_col=0)
sgtembedding_test_pname_and_sid = pd.read_csv('processed_data/SGT/Combined Features/sgt_test_pname_and_sid April 2.csv',index_col=0)

del sgtembedding_train_pname_and_sid['id']
del sgtembedding_test_pname_and_sid['id']

from sklearn.decomposition import PCA
pca = PCA(n_components=150)
pca.fit(sgtembedding_train_pname_and_sid)
sgtembedding_train_pname_and_sid = pca.transform(sgtembedding_train_pname_and_sid)
sgtembedding_test_pname_and_sid = pca.transform(sgtembedding_test_pname_and_sid)
sgtembedding_train_pname_and_sid = pd.DataFrame(data=sgtembedding_train_pname_and_sid, columns=[i for i in range(sgtembedding_train_pname_and_sid.shape[1])])
sgtembedding_test_pname_and_sid = pd.DataFrame(data=sgtembedding_test_pname_and_sid, columns=[i for i in range(sgtembedding_test_pname_and_sid.shape[1])])

print(np.sum(pca.explained_variance_ratio_))
# 25 0.8077329873418991
# 50 0.927464010137707
# 75 0.9687909053936339
# 100 0.9831622087487326
# 125 0.9899795046641106
# 150 0.9939427575919144
# 175 0.9963970796504291
# 200 0.9979145853624205
# 225 0.9987524549964832

0.9939298517316316


### stay time & lagg

In [ ]:
# sgtembedding_train_stay_time_and_lagg = pd.read_csv('processed_data/SGT/Combined Features/sgt_train_stay_time_and_lagg April 2.csv',index_col=0)
# sgtembedding_test_stay_time_and_lagg = pd.read_csv('processed_data/SGT/Combined Features/sgt_test_stay_time_and_lagg April 2.csv',index_col=0)

# del sgtembedding_train_stay_time_and_lagg['id']
# del sgtembedding_test_stay_time_and_lagg['id']

# from sklearn.decomposition import PCA
# pca = PCA(n_components=500)
# pca.fit(sgtembedding_train_stay_time_and_lagg)
# sgtembedding_train_stay_time_and_lagg = pca.transform(sgtembedding_train_stay_time_and_lagg)
# sgtembedding_test_stay_time_and_lagg = pca.transform(sgtembedding_test_stay_time_and_lagg)
# sgtembedding_train_stay_time_and_lagg = pd.DataFrame(data=sgtembedding_train_stay_time_and_lagg, columns=[i for i in range(sgtembedding_train_stay_time_and_lagg.shape[1])])
# sgtembedding_test_stay_time_and_lagg = pd.DataFrame(data=sgtembedding_test_stay_time_and_lagg, columns=[i for i in range(sgtembedding_test_stay_time_and_lagg.shape[1])])

# print(np.sum(pca.explained_variance_ratio_))
# # 200 0.565784288168497
# # 250 0.6434229033482115
# # 300 0.7120764079780737
# # 350 0.7731413082181554
# # 400 0.8277161511268518
# # 450 0.8767201127925517
# # 500 0.9244176250355233
# # 550 0.9608767327029049

## Concatnate combined features with single features

In [ ]:
# Import training and test set with SGT features
train = pd.read_csv('processed_data/SGT/sgt_train_all April 2.csv', index_col=0)
test = pd.read_csv('processed_data/SGT/sgt_test_all April 2.csv', index_col=0)

In [ ]:
# Concat features
train = pd.concat([train, sgtembedding_train_pname_and_stay_time, sgtembedding_train_pname_and_lagg, sgtembedding_train_pname_and_pid, sgtembedding_train_pname_and_sid], axis=1) 
#
test = pd.concat([test, sgtembedding_test_pname_and_stay_time, sgtembedding_test_pname_and_lagg, sgtembedding_test_pname_and_pid, sgtembedding_test_pname_and_sid], axis=1) 
#
train.columns = [i for i in range(len(train.columns))]
test.columns = [i for i in range(len(test.columns))]

In [ ]:
# train = train.rename(columns = lambda x:re.sub('[^A-Za-z0-9_]+', '', x))
# test = test.rename(columns = lambda x:re.sub('[^A-Za-z0-9_]+', '', x))

In [ ]:
# weight = (data['label'] == 1).sum()/(data['label'] == 0).sum()

## Combined features model training

In [ ]:
data = pd.read_csv('processed_data/SGT/page only training April 2.csv')
test_data = pd.read_csv('processed_data/SGT/page only testing April 2.csv')
test_data['label']=0
test_data.loc[test_data['overdue']>5,'label']=1

In [ ]:
X_train, X_val, y_train, y_val = train_test_split(train, data['label'],
                                               train_size = 1 - 0.1,
                                               test_size = 0.1,
                                               random_state = 111,
                                               shuffle = True)

In [ ]:
categorical_features_indices = np.where(train.dtypes != np.float)[0]

model = CatBoostClassifier(
    iterations=9999999,
    learning_rate=0.002,
    task_type='GPU',
    custom_metric=['Logloss', 'AUC'],
    objective='Logloss',
    eval_metric='AUC',
    random_seed = 20210401,
#     gpu_ram_part=0.9,
#     boosting_type='Plain',
#     max_ctr_complexity=2,
#     depth=6,
#     gpu_cat_features_storage='CpuPinnedMemory',
)


model.fit(X_train, y_train,
    eval_set=(X_val, y_val),
    cat_features=categorical_features_indices,
    early_stopping_rounds=3000,
    # verbose=10,
    plot=True
)


model.get_feature_importance(prettified=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

流式输出内容被截断，只能显示最后 5000 行内容。
26358:	learn: 0.7983209	test: 0.6497171	best: 0.6497236 (26319)	total: 15m 6s	remaining: 3d 23h 14m 7s
26359:	learn: 0.7983247	test: 0.6497194	best: 0.6497236 (26319)	total: 15m 6s	remaining: 3d 23h 14m 6s
26360:	learn: 0.7983298	test: 0.6497244	best: 0.6497244 (26360)	total: 15m 6s	remaining: 3d 23h 14m 11s
26361:	learn: 0.7983336	test: 0.6497223	best: 0.6497244 (26360)	total: 15m 6s	remaining: 3d 23h 14m 13s
26362:	learn: 0.7983404	test: 0.6497221	best: 0.6497244 (26360)	total: 15m 6s	remaining: 3d 23h 14m 15s
26363:	learn: 0.7983441	test: 0.6497222	best: 0.6497244 (26360)	total: 15m 6s	remaining: 3d 23h 14m 14s
26364:	learn: 0.7983473	test: 0.6497191	best: 0.6497244 (26360)	total: 15m 6s	remaining: 3d 23h 14m 13s
26365:	learn: 0.7983526	test: 0.6497200	best: 0.6497244 (26360)	total: 15m 6s	remaining: 3d 23h 14m 12s
26366:	learn: 0.7983559	test: 0.6497200	best: 0.6497244 (26360)	total: 15m 6s	remaining: 3d 23h 14m 12s
26367:	learn: 0.7983596	test: 0.6497181

Feature Id  Importances
0           121     6.084846
1           941     1.361504
2           234     1.026447
3            48     0.849991
4           259     0.789162
...         ...          ...
1178         31     0.000000
1179         64     0.000000
1180         86     0.000000
1181        108     0.000000
1182        109     0.000000

[1183 rows x 2 columns]

### Result

In [ ]:
# Result： Baseline: 0.6399

## 1. only pname & stay time： PCA(300)
### 0.6442 PCA(250) CatBoost(lr=0.005,early=1000)
### 0.6444 PCA(275)
##* 0.6445 PCA(300) CatBoost(lr=0.003,early=1200) 
### 0.6438 PCA(325) 
### 0.6441 PCA(400) CatBoost(lr=0.003,early=3000) 

## 2. only pname & lagg： PCA(400)
### 0.6403 PCA(225)
### 0.6404 PCA(250)
##* 0.6407 PCA(400) CatBoost(lr=0.003,early=2000)

## 3. only pname & pid: PCA(100)
##* 0.6423 PCA(100) CatBoost(lr=0.003,early=2000)
### 0.6423 PCA(100) CatBoost(lr=0.005,early=2000)

## 4. only pname & sid: PCA(150)
##* 0.6413 PCA(150) CatBoost(lr=0.005,early=2000)
### 0.6410 PCA(150) CatBoost(lr=0.003,early=3000)

## 5. only stay time & lagg
### 0.6382 PCA(500)

## pname & stay time, pname & lagg：
### 0.6448 PCA(250) PCA(250) CatBoost(lr=0.005,early=1000)
### 0.6457 PCA(300) PCA(250) CatBoost(lr=0.005,early=1000)
### 0.6463 PCA(300) PCA(250) CatBoost(lr=0.003,early=1200)

## pname & stay time, pname & lagg, stay time & lagg


## all
### 0.6476 CatBoost(lr=0.01,early=3000)
### 0.6482 CatBoost(lr=0.003,early=3000)
### 0.6491 CatBoost(lr=0.002,early=3000,iter=30000)  0.2204
y_pred=model.predict_proba(test)[:,1]
labels = test_data['label']
auc = roc_auc_score(labels, y_pred)
print("Test AUC: {}".format(auc))

Test AUC: 0.6490568681042035


In [ ]:
def ks(preds, train_data):
    '''
    This function is to calculate the ks score given the true label and 
    prediction distribution. It can be used as the evaluation function in the 
    model to select the model with the highest KS score.
    '''
    labels = train_data.get_label()
    preds = 1. / (1. + np.exp(-preds))
    fpr, tpr, threshold = roc_curve(labels, preds)
    ks = (tpr-fpr)
    return 'ks', np.max(ks), True
fpr, tpr, threshold = roc_curve(labels, y_pred)
ks = (tpr-fpr)
max_ = np.argmax(ks)
print("Test KS:", np.max(ks))

Test KS: 0.22036293044638178


## Baseline Models

### Baseline(0.6399): New Single Features Output(stay time, lagg divided into 5 cats)

In [ ]:
cat_features = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21]
#
categorical_features_indices = np.where(train.dtypes != np.float)[0]

model = CatBoostClassifier(
    iterations=20000,
    learning_rate=0.005,
    task_type='GPU',
    custom_metric=['Logloss', 'AUC'],
    objective='Logloss',
    eval_metric='AUC',
    random_seed = 20210401,
#     gpu_ram_part=0.9,
#     boosting_type='Plain',
#     max_ctr_complexity=2,
#     depth=6,
#     gpu_cat_features_storage='CpuPinnedMemory',
)


model.fit(X_train, y_train,
    eval_set=(X_val, y_val),
    cat_features=categorical_features_indices,
    early_stopping_rounds=1000,
    # verbose=10,
    plot=True
)


model.get_feature_importance(prettified=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

流式输出内容被截断，只能显示最后 5000 行内容。
4269:	learn: 0.6955908	test: 0.6401564	best: 0.6401752 (4247)	total: 1m 27s	remaining: 5m 22s
4270:	learn: 0.6955987	test: 0.6401636	best: 0.6401752 (4247)	total: 1m 27s	remaining: 5m 22s
4271:	learn: 0.6956084	test: 0.6401676	best: 0.6401752 (4247)	total: 1m 27s	remaining: 5m 22s
4272:	learn: 0.6956128	test: 0.6401615	best: 0.6401752 (4247)	total: 1m 27s	remaining: 5m 22s
4273:	learn: 0.6956244	test: 0.6401727	best: 0.6401752 (4247)	total: 1m 27s	remaining: 5m 22s
4274:	learn: 0.6956338	test: 0.6401713	best: 0.6401752 (4247)	total: 1m 27s	remaining: 5m 22s
4275:	learn: 0.6956406	test: 0.6401707	best: 0.6401752 (4247)	total: 1m 27s	remaining: 5m 22s
4276:	learn: 0.6956508	test: 0.6401652	best: 0.6401752 (4247)	total: 1m 27s	remaining: 5m 21s
4277:	learn: 0.6956694	test: 0.6401609	best: 0.6401752 (4247)	total: 1m 27s	remaining: 5m 21s
4278:	learn: 0.6956801	test: 0.6401547	best: 0.6401752 (4247)	total: 1m 27s	remaining: 5m 21s
4279:	learn: 0.6956920	test: 0.64

Feature Id  Importances
0          121    10.530866
1           48     3.903062
2           70     2.314676
3          136     1.496056
4          131     1.389599
..         ...          ...
228         76     0.000135
229         20     0.000121
230         86     0.000108
231        109     0.000062
232         64     0.000047

[233 rows x 2 columns]

In [ ]:
y_pred=model.predict_proba(test)[:,1]
labels = test_data['label']
auc = roc_auc_score(labels, y_pred)
print("Test AUC: {}".format(auc))

Test AUC: 0.6398877245301531


### (0.6431)Original Single features output(stay time, lagg divided into 10 cats)

In [ ]:
y_pred=model.predict_proba(test)[:,1]
labels = test_data['label']
auc = roc_auc_score(labels, y_pred)
print("Test AUC: {}".format(auc))

Test AUC: 0.6431383008006428
